In [1]:
WEB_SITE_NAME = 'Paroshat.com'

In [2]:
WEB_SITE_matrix = '../../models/' + WEB_SITE_NAME + '/view_matrix/lil_matrix.npz'
WEB_SITE_CONTENT_CSV = '../../models/content/' + WEB_SITE_NAME + '.csv'
WEB_SITE_itemindexer = '../../models/' + WEB_SITE_NAME + '/view_matrix/item_indexer.indexer'
WEB_SITE_userindexer = '../../models/' + WEB_SITE_NAME + '/view_matrix/user_indexer.indexer'
SAVING_ITEM_INDEXER = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_item_indexer_factorized.indexer'
SAVING_USER_INDEXER = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_user_indexer_factorized.indexer'
SAVING3 = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_items_vectors.npy'
SAVING4 = './alisResult/' + WEB_SITE_NAME + '/ALS/ali_users_vectors.npy'
RESULTS = '../results/' + WEB_SITE_NAME + '/'
USER_MIN_VIEWS = 3
ITEM_MIN_VIEWS = 4

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import colors
from matplotlib.ticker import PercentFormatter
from tqdm import tqdm

import timeit
import time
import math

# ./indexer
from indexer import AppendIndexer
import ALS

# Annoy
from annoy import AnnoyIndex

#SKLearn 
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import average_precision_score
from sklearn.metrics import pairwise_distances
from sklearn.model_selection import train_test_split

# scipy
from scipy.spatial import distance
from scipy.sparse import lil_matrix

In [4]:
WEBSITE_content = pd.read_csv(WEB_SITE_CONTENT_CSV)
print(WEBSITE_content.shape)
WEBSITE_content.tail(50)

(5443, 17)


Unnamed: 0       id                           created  \
5393      148138  8395834  2020-11-26 15:00:12.956968+03:30   
5394      148165  8396760  2020-11-26 16:10:12.817303+03:30   
5395      148224  8398426  2020-11-26 18:40:51.490291+03:30   
5396      148232  8398647  2020-11-26 19:00:14.802227+03:30   
5397      148251  8399457  2020-11-26 20:17:25.719524+03:30   
5398      148345  8401737  2020-11-26 23:42:44.782526+03:30   
5399      148429  8407807  2020-11-27 07:10:10.437904+03:30   
5400      148432  8407786  2020-11-27 07:05:08.486496+03:30   
5401      148434  8407808  2020-11-27 07:10:10.439292+03:30   
5402      148435  8407809  2020-11-27 07:10:10.440384+03:30   
5403      148436  8407833  2020-11-27 07:15:16.146759+03:30   
5404      148437  8407834  2020-11-27 07:15:16.147941+03:30   
5405      148438  8407835  2020-11-27 07:15:16.149093+03:30   
5406      148439  8407836  2020-11-27 07:15:16.150311+03:30   
5407      148440  8407837  2020-11-27 07:15:16.151468+03:30   
5408      148478  8409275  2020-11-27 10:35:09.534125+03:30   
5409      148509  8410750  2020-11-27 12:30:12.276406+03:30   
5410      148514  8410919  2020-11-27 12:46:13.598159+03:30   
5411      148683  8417244  2020-11-27 21:25:18.574923+03:30   
5412      148711  8418016  2020-11-27 22:15:39.056033+03:30   
5413      148722  8418538  2020-11-27 22:55:11.950063+03:30   
5414      148732  8418757  2020-11-27 23:10:13.449684+03:30   
5415      148823  8422564  2020-11-28 03:20:13.310266+03:30   
5416      149037  8430917  2020-11-28 16:20:16.778452+03:30   
5417      149068  8431995  2020-11-28 17:30:15.645132+03:30   
5418      149076  8432178  2020-11-28 17:45:11.758617+03:30   
5419      149269  8438296  2020-11-29 01:48:44.250263+03:30   
5420      149279  8438412  2020-11-29 02:06:19.046939+03:30   
5421      149281  8438491  2020-11-29 02:09:31.650878+03:30   
5422      149286  8438735  2020-11-29 02:34:56.113881+03:30   
5423      149287  8438736  2020-11-29 02:34:56.115303+03:30   
5424      149289  8438760   2020-11-29 02:38:15.29593+03:30   
5425      149291  8438813  2020-11-29 02:46:16.292055+03:30   
5426      149292  8439060  2020-11-29 03:01:43.382441+03:30   
5427      149293  8439164  2020-11-29 03:26:18.825494+03:30   
5428      149346  8441273  2020-11-29 10:31:46.613241+03:30   
5429      149407  8447229  2020-11-29 22:40:14.158071+03:30   
5430      149433  8448369   2020-11-29 23:45:14.32023+03:30   
5431      149491  8450372  2020-11-30 01:20:16.657999+03:30   
5432      149557  8453064  2020-11-30 04:05:13.474378+03:30   
5433      149624  8455383  2020-11-30 09:40:15.684531+03:30   
5434      149636  8455867   2020-11-30 10:35:13.87518+03:30   
5435      149668  8456797  2020-11-30 12:15:14.333938+03:30   
5436      149687  8457669  2020-11-30 13:40:16.348988+03:30   
5437      149759  8460012  2020-12-01 14:27:57.340605+03:30   
5438      149760  8460013  2020-12-01 14:27:57.342179+03:30   
5439      149761  8460014  2020-12-01 14:27:57.344515+03:30   
5440      149762  8460015  2020-12-01 14:27:57.346991+03:30   
5441      149763  8460016   2020-12-01 14:27:57.34938+03:30   
5442      149764  8460017   2020-12-01 14:27:57.35069+03:30   

                                         content_vector  \
5393  {-0.117065452039242,-0.763847470283508,-1.1492...   
5394  {0.684478163719177,0.564636766910553,-0.568408...   
5395  {0.625571131706238,-0.505210757255554,-1.09345...   
5396  {0.498680979013443,-0.578286945819855,-0.28032...   
5397  {0.619594275951385,0.660922944545746,-0.934755...   
5398  {1.86573076248169,0.405868023633957,-0.7641263...   
5399  {0.312241315841675,-0.146932557225227,0.176717...   
5400  {0.312241315841675,-0.146932557225227,0.176717...   
5401  {0.312241315841675,-0.146932557225227,0.176717...   
5402  {0.312241315841675,-0.146932557225227,0.176717...   
5403  {0.312241315841675,-0.146932557225227,0.176717...   
5404  {0.312241315841675,-0.146932557225227,0.176717...   
5405  {0.312241315841675,

In [5]:
WEBSITE_content = WEBSITE_content[WEBSITE_content.included == 't']
WEBSITE_content.shape

(4678, 17)

In [6]:
class ViewMatrix:
    def __init__(self, path):
        self.path = path
        self.original = True
        self.item_indexer = AppendIndexer.load(WEB_SITE_itemindexer)
        self.user_indexer = AppendIndexer.load(WEB_SITE_userindexer)
        
    def load_matrix(path):
        
        matrix = ViewMatrix(path)
        try:
            matrix.view_matrix = ViewMatrix \
                .load_sparse_lil(path)
        except:
            print('Error: loading', path)

        return matrix

    def load_sparse_lil(filename):
        loader = np.load(filename, allow_pickle=True)
        result = lil_matrix(tuple(loader["shape"]), dtype=str(loader["dtype"]))
        result.data = loader["data"]
        result.rows = loader["rows"]
        return result
    
    def make_dense(self, user_min_view, item_min_view):
        self.original = False
        while True:
            removed_rows_cnt = self.trim_users_with_few_views(user_min_view)
            removed_columns_cnt = self.trim_columns_with_few_views(item_min_view)
            if not removed_columns_cnt and not removed_rows_cnt:
                break

    def trim_users_with_few_views(self, user_min_view):
        removing_row_indices = list(np.where(self.view_matrix.getnnz(1) < user_min_view)[0])
        print('Number of users which should be deleted:', len(removing_row_indices))
        self.trim_user_indices(to_remove_indices=removing_row_indices)
        return len(removing_row_indices)

    def trim_columns_with_few_views(self, column_min_view):
        removing_column_indices = list(np.where(self.view_matrix.getnnz(0) < column_min_view)[0])
        print('Number products which should be deleted:', len(removing_column_indices))
        self.trim_column_indices(to_remove_indices=removing_column_indices)
        return len(removing_column_indices)
    
    def trim_user_indices(self, to_remove_indices):
        self.user_indexer.remove_indexes(to_remove_indices)
        self.view_matrix = ViewMatrix.delete_row_lil(self.view_matrix, to_remove_indices)
    
    def trim_column_indices(self, to_remove_indices):
        self.item_indexer.remove_indexes(to_remove_indices)
        self.view_matrix = ViewMatrix.delete_column_lil(self.view_matrix, to_remove_indices)
    
    def delete_column_lil(mat: lil_matrix, *i) -> lil_matrix:
        mat = mat.transpose()
        mat = ViewMatrix.delete_row_lil(mat, *i)
        return mat.transpose()
    
    def delete_row_lil(mat: lil_matrix, *i) -> lil_matrix:
        if not isinstance(mat, lil_matrix):
            raise ValueError("works only for LIL format -- use .tolil() first")
        mat = mat.copy()
        mat.rows = np.delete(mat.rows, i)
        mat.data = np.delete(mat.data, i)
        mat._shape = (mat.rows.shape[0], mat._shape[1])
        return mat
    def to_csr(self):
        train_data = self.view_matrix.astype(np.float64)
        train_data = train_data.tocoo()
        train_data.data = np.log10(train_data.data) + 1
        train_data = train_data.tocsr()
        return train_data

In [7]:
def CFTrain(path: str, _alpha = 20, factors = 20):
    now = time.time()
    matrix = ViewMatrix.load_matrix(path)
    print('View matrix loaded in', time.time() - now, 'seconds.')

    now = time.time()
    sparce_matrix = matrix.to_csr()
    matrix.make_dense(user_min_view = USER_MIN_VIEWS, 
                      item_min_view = ITEM_MIN_VIEWS)
    print('matrix has been made dense in', time.time() - now, 'seconds.')

    als_model = ALS.Als(num_factors = 60,
                        iterations = 15,
                        num_threads = 15,
                        alpha = 100)

    implicit_matrix = matrix.to_csr()
    
    now = time.time()
    print("implicit_matrix shape", implicit_matrix.shape)
    als_model.fit(implicit_matrix)
    alsTime = time.time() - now
    print('ALS model is fitted in', time.time() - now, 'seconds.')
    
    print('Saving Data ...')
    matrix.item_indexer.dump(SAVING_ITEM_INDEXER)
    matrix.user_indexer.dump(SAVING_USER_INDEXER)
    np.save(SAVING3, als_model.item_vectors)
    np.save(SAVING4, als_model.user_vectors)
    
    return sparce_matrix, implicit_matrix, als_model.item_vectors, als_model.user_vectors, matrix.item_indexer, matrix.user_indexer, alsTime

In [8]:
sparce_matrix, implicit_matrix, item_vectors, user_vectors, item_indexer, user_indexer, alsTime = \
CFTrain(WEB_SITE_matrix, factors = 60)

View matrix loaded in 10.348867177963257 seconds.
Number of users which should be deleted: 4179077
Number products which should be deleted: 6434
Number of users which should be deleted: 386
Number products which should be deleted: 29
Number of users which should be deleted: 28
Number products which should be deleted: 2
Number of users which should be deleted: 0
Number products which should be deleted: 0
matrix has been made dense in 12.25952410697937 seconds.
implicit_matrix shape (14811, 1725)
ALS model is fitted in 10.800974607467651 seconds.
Saving Data ...


In [9]:
ids = WEBSITE_content['id'].tolist()

In [10]:
print(item_vectors.shape)

(1725, 60)


In [11]:
print('sparce matrix:\t', sparce_matrix.shape)
print('implicit matrix:', implicit_matrix.shape)
print('item vectors:\t', item_vectors.shape)
print('users vectors:\t', user_vectors.shape)

sparce matrix:	 (4194302, 8190)
implicit matrix: (14811, 1725)
item vectors:	 (1725, 60)
users vectors:	 (14811, 60)


In [12]:
print('user tokens:\t', np.array(list(user_indexer.get_items())).shape)
print('item ids:\t', np.array(list(item_indexer.get_items())).shape)

user tokens:	 (14811,)
item ids:	 (1725,)


## Vectorized

In [88]:
ratings = user_vectors.dot(item_vectors.T)
print(ratings.shape)

(14811, 1725)


In [89]:
row, col = implicit_matrix.nonzero()
for i, j in zip(row, col):
    ratings[i, j] = -1
users_recoms2 = []
for user_ratings in tqdm(ratings):
    recoms = np.argsort(user_ratings)[-13:][::-1]
#     print(recoms)
    user_recoms = []
    for r in recoms:
        rec = item_indexer.reverse_get(r)
        if int(rec) in ids:
#             user_recoms.append(r)
            user_recoms.append(rec)
#     print(user_recoms)
    users_recoms2.append(user_recoms)

100%|██████████| 14811/14811 [00:07<00:00, 1940.09it/s]


In [90]:
users = list(user_indexer.get_items())
print(len(users_recoms2), len(list(user_indexer.get_items())))

14811 14811


## batch

In [120]:
user_ranges = [i for i in range(0,len(user_vectors),1000)]
user_ranges.append(len(user_vectors))
item_ranges = [i for i in range(0,len(item_vectors),1000)]
item_ranges.append(len(item_vectors))

In [121]:
print(item_ranges)
print(user_ranges)

[0, 1000, 1725]
[0, 1000, 2000, 3000, 4000, 5000, 6000, 7000, 8000, 9000, 10000, 11000, 12000, 13000, 14000, 14811]


In [122]:
users_recoms = []
temporary = []
for i in tqdm(range(len(user_ranges)-1)):
    m = []
    for j in range(len(item_ranges)-1):
        temp = user_vectors[user_ranges[i]:user_ranges[i+1]].dot(item_vectors[item_ranges[j]:item_ranges[j+1]].T)
        if not len(m):
            m = temp
        else:
            m = np.concatenate((m, temp), 1)
    row, col = implicit_matrix[user_ranges[i]:user_ranges[i+1],:].nonzero()
    for i, j in zip(row, col):
        m[i, j] = -1
    if not len(temporary):
        temporary = m
    else:
        np.concatenate((temporary, m), 0)
    for user_ratings in m:
        recoms = np.argsort(user_ratings)[-13:][::-1]
        user_recoms = []
        for r in recoms:
            rec = item_indexer.reverse_get(r)
            if int(rec) in ids:
    #             user_recoms.append(r)
                user_recoms.append(rec)
        users_recoms.append(user_recoms)

100%|██████████| 15/15 [00:08<00:00,  1.81it/s]


In [123]:
users = list(user_indexer.get_items())
print(len(users_recoms), len(list(user_indexer.get_items())))

14811 14811


## check

In [129]:
def check(h, user_num = 100):
    row, col = implicit_matrix.nonzero()
    print('---user:', users[user_num], '---')
    print('what user saw:')
    for i in col[row == user_num]:
        print(WEBSITE_content[WEBSITE_content['id'] == int(item_indexer.reverse_get(i))].title.values)
    print('what we recommend:')
    for i in h[user_num]:
        print(WEBSITE_content[WEBSITE_content['id'] == int(i)].title.values)

In [130]:
for i in range(0,len(users_recoms), 14):
    print(i)
    check(users_recoms, i)

0
---user: 02fb517a-85ee-4e5e-ce00-50c8f3c384d2 ---
what user saw:
['معرفی 25 فیلم با پیچیده ترین پایان بندی ها در تاریخ سینما - پروشات']
['12 فیلم برتر تاریخ سینما با محوریت CIA (سازمان سیا) - پروشات']
['لیست بهترین فیلم هایی که با موضوع فرار از زندان ساخته شده اند - پروشات']
['معرفی 10 فیلم جذاب و دیدنی درباره تروریسم که شاید دوست داشته باشید تماشا کنید - پروشات']
what we recommend:
['20 فیلم برتر ژانر آدم ربایی در تاریخ سینما که باید ببینید - پروشات']
['25 فیلم روان شناسی تاریخ سینما که اثری عمیق روی شما می گذارند - پروشات']
['10 فیلم انتقامی برتر تاریخ سینما که باید ببینید - پروشات']
['معرفی بهترین فیلم های تاریخ سینما با موضوع اعتیاد و مواد مخدر - پروشات']
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['معرفی 26 فیلم جذاب و دیدنی درباره سرقت در تاریخ سینما که باید تماشا کنید - پروشات']
['معرفی 20 فیلم برتر سینما که ذهن بیننده را به چالش می کشند - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروش

['لیست بهترین انیمه های جهان، 21 انیمه سینمایی برای چند بار دیدن! - پروشات']
154
---user: cd0c4d50-0847c-c54de-e21f8-8c233981e582e ---
what user saw:
['اگر به بازی GTA علاقه دارید، این 10 بازی را از دست ندهید - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروشات']
['معرفی تمام فیلم های تام کروز از بدترین تا بهترین، 42 اثر سینمایی پرخرج - پروشات']
['9 فیلم جذاب و دیدنی شبیه فیلم "لوسی" (Lucy) که باید تماشا کنید - پروشات']
['معرفی 30 فیلم جذاب و دیدنی شبیه "تلقین" (Inception) - پروشات']
['50 بازی برتر در تاریخ بازی های کامپیوتری: از نوستالژیک ها تا مدرن ها - پروشات']
['50 بازی برتر در تاریخ بازی های کامپیوتری: از نوستالژیک ها تا مدرن ها - صفحه 3 از 5 - پروشات']
['50 بازی برتر در تاریخ بازی های کامپیوتری: از نوستالژیک ها تا مدرن ها - صفحه 2 از 5 - پروشات']
['لیست بهترین فیلم\u200cهای جانی دپ که باید تماشا کنید']
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
what we recommend:
['50 بازی برتر در تاریخ بازی های کامپیوتری: از نوست

['12 فیلم جذاب و دیدنی شبیه فیلم "8 مایل" (8 Mile) - پروشات']
[]
['معرفی 12 سریال جذاب و دیدنی با مدت زمان 20 تا 30 دقیقه - پروشات']
what we recommend:
['بهترین سریال\u200cهای فانتزی و علمی-تخیلی براساس امتیاز IMDb']
['معرفی 13 سریال جذاب و دیدنی با ژانر فراطبیعی در تاریخ سینما که نباید از دست بدهید - پروشات']
['معرفی 25 فیلم برتر موزیکال و رقص در تاریخ سینما - پروشات']
['لیست بهترین سریال های کره ای در سال 2018 - پروشات']
['معرفی بهترین سریال\u200cهای کره\u200cای این دهه (2019 تا 2010) - پروشات']
['بهترین سریال های کره ای عاشقانه و درام که نباید از دست بدهید - پروشات']
['لیست بهترین سریال\u200cهای کره\u200cای سال 2020 که در انتظار پخششان هستیم - پروشات']
['بهترین سریال های درام کره ای که در سال 2019 پخش خواهند شد - پروشات']
['معرفی 18 سریال جذاب و دیدنی شبیه "دختر جدید" (New Girl) - پروشات']
['بهترین فیلم\u200cهای عجیب کمدی که شاید تا به حال تماشا نکرده باشید']
['7 فیلم جذاب و دیدنی شبیه فیلم "بعد از برخورد ما" (After We Collided) که باید تماشا کنید - پروشات']
336
---user: 0f6d13c1-58

['معرفی 12 سریال جذاب و دیدنی شبیه "تاج" (The Crown) - پروشات']
['لیست بهترین سریال\u200cهای کره\u200cای سال 2020 که در انتظار پخششان هستیم - پروشات']
['7 سریال جذاب و دیدنی شبیه سریال "گامبی ملکه" (The Queen’s Gambit) که باید تماشا کنید - پروشات']
['معرفی 15 سریال جذاب و دیدنی شبیه "خاطرات خون آشام" (The Vampire Diaries) - پروشات']
['معرفی 10 لایو اکشن پرفروش تاریخ دیزنی در باکس\u200cآفیس - پروشات']
['آخر هفته با طعم فیلم! (شماره 114)']
['25 درام برتر سینمای کره جنوبی - پروشات']
['لیست بهترین سریال های کره ای در سال 2018 - پروشات']
['معرفی 13 سریال جذاب و دیدنی با ژانر فراطبیعی در تاریخ سینما که نباید از دست بدهید - پروشات']
['بهترین فیلم\u200cهای کره جنوبی در قرن بیست و یک که باید تماشا کنید']
['معرفی 18 فیلم غم انگیز تاریخ سینما - پروشات']
532
---user: 80301bcf-aaac-45f8-c5a9-ea4d3a185eb3 ---
what user saw:
['طبقه بندی 10 جوکر قدرتمند تاریخ سینما - پروشات']
['10 شخصیت مارول که از دی سی الهام گرفته شده اند - پروشات']
['5 ابرقهرمان DC که می\u200cتوانند بیوه سیاه مارول را شکست دهند (و 

---user: 026c64d1-16c2f-f3d7e-e7337-7805055459744 ---
what user saw:
['معرفی 10 انیمه جذاب و دیدنی با ژانر حارم در سال 2019 که باید تماشا کنید - پروشات']
['معرفی 20 انیمه مورد انتظار سال 2020 که در انتظار انتشارشان هستیم - پروشات']
['لیست انیمه ۹ تا از بهترین انیمه\u200cهای چینی به انتخاب پروشات - پروشات']
what we recommend:
['معرفی تمام ژانرهای انیمه و مانگا به همراه انیمه لیست و توضیحات کامل - پروشات']
['strike-the-blood - پروشات']
['14 انیمه اکشن رمانتیک برتر همه زمان ها - پروشات']
['12 انیمه جذاب و دیدنی با موضوع خون آشامی - پروشات']
['معرفی 12 انیمه برتر ژانر ایسکای در تاریخ انیمه سازی - پروشات']
['انیمه لیست 50 تایی از بهترین انیمه های سریالی تاریخ به انتخاب پروشات - پروشات']
['۵ انیمه شبیه "Tensei shitara Slime Datta Ken" که باید تماشا کنید - پروشات']
['7 انیمه جذاب و دیدنی شبیه انیمه "بی نظم در دبیرستان جادو" (The Irregular at Magic High School) - پروشات']
['لیست بهترین انیمه های 2018 که حتما باید ببینید - پروشات']
['11 انیمه برتر تاریخ با موضوع فرشتگان که باید ببینید - پروشات'

...

['حقایق جالب و ناگفته درباره آریانا گرانده - پروشات']
['بیوگرافی کامل تسا تامپسون (Tessa Thompson) از کودکی تا به امروز - پروشات']
['لیست بهترین فیلم\u200cهای جیم کری، ستاره سرشناس ژانر کمدی هالیوود - پروشات']
['بیوگرافی کامل الیزابت اولسن (Elizabeth Olsen) از کودکی تا به امروز - پروشات']
['بیوگرافی کامل کیلین مورفی (Cillian Murphy) از کودکی تا به امروز - پروشات']
['30 حقیقت جالب درباره مگان فاکس + تصاویر - پروشات']
['معرفی بهترین فیلم های عاشقانه قرن 21 که احساسات شما را برانگیخته می\u200cکنند - پروشات']
13706
---user: ccca9e7a-aef65-54745-5bc35-52e6b5819f6e1 ---
what user saw:
['بهترین انیمه هایی که در سال 2019 و 2020 منتظر اکران شان هستیم - پروشات']
['لیست 30 شخصیت برتر در تاریخ انیمه ها - پروشات']
[]
['معرفی 15 انیمه سریالی جذاب و دیدنی شبیه "نوراگامی" (Noragami) - پروشات']
['معرفی 10 انیمه سریالی جذاب و دیدنی برای طرفداران انیمه - پروشات']
['معرفی 12 انیمه جذاب و دیدنی که در بهار 2020 پخش شدند - پروشات']
['معرفی 20 شخصیت قدرتمند انیمه\u200cها که از "ناروتو" قوی\u200cتر هستند - پرو

---user: 4c5fffdd-ded90-09f09-9973b-bfb98b1774af3 ---
what user saw:
['لیست بهترین سریال\u200cهای کره\u200cای سال 2020 که در انتظار پخششان هستیم - پروشات']
['بهترین فیلم های سینمایی کره ای رمانتیک که باید ببینید - پروشات']
['لیست بهترین فیلم\u200cهای عاشقانه سال 2020 که در انتظار اکرانشان هستیم - پروشات']
what we recommend:
['بهترین سریال های کره ای عاشقانه و درام که نباید از دست بدهید - پروشات']
['بهترین سریال های درام کره ای که در سال 2019 پخش خواهند شد - پروشات']
['لیست بهترین سریال های کره ای در سال 2018 - پروشات']
['25 درام برتر سینمای کره جنوبی - پروشات']
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
['معرفی بهترین سریال\u200cهای کره\u200cای این دهه (2019 تا 2010) - پروشات']
['معرفی بهترین فیلم های عاشقانه قرن 21 که احساسات شما را برانگیخته می\u200cکنند - پروشات']
['7 فیلم جذاب و دیدنی شبیه فیلم "بعد از برخورد ما" (After We Collided) که باید تماشا کنید - پروشات']
['معرفی 15 فیلم جذاب و دیدنی شبیه "پنجاه طیف خاکستری" (Fifty Shades of Grey) - پرو

['لیست بهترین فیلم\u200cهای فمینیستی تاریخ سینما که باید تماشا کنید']
['لیست بهترین فیلم\u200cهای عجیب و غریب تاریخ سینما که باید تماشا کنید']
['آخر هفته با طعم فیلم! (شماره 113)']
['10 فیلم برتر جکی چان که ارزش چند بار دیدن را دارند - پروشات']
['معرفی بهترین فیلم\u200cهای “فدریکو فلینی” به مناسبت صدسالگی این کارگردان ایتالیایی']
['معرفی فیلم کره\u200cای “آب\u200cنبات نعنایی” (Peppermint Candy)']
14154
---user: dee011ef-12f6-4775-c701-2d50b0caf157 ---
what user saw:
['لیست 24 تایی طولانی ترین انیمه های سریالی که تاکنون ساخته شده اند - پروشات']
['بهترین انیمه های شبیه “شیطان کش” (Demon Slayer: Kimetsu no Yaiba)']
['بهترین انیمه های مشابه “ناکجا آباد موعود” (The Promised Neverland)']
what we recommend:
['معرفی بهترین انیمه های مشابه “موشوکو تنسی:تجسم بیکاری”']
['7 انیمه جذاب و دیدنی شبیه “هوریمیا” (Horimiya) که باید تماشا کنید']
['بهترین انیمه های مشابه “پنج قلوهای باکلاس” (The Quintessential Quintuplets)']
['بهترین انیمه های مشابه “سامورایی چامپلو” (The Samurai Champloo)']
['7 انیمه جذا

[]
['پروشات - صفحه 7 از 348 - مجله آنلاین سینما و سرگرمی']
['لیست محبوب\u200cترین شخصیت\u200cهای “توئین پیکس” (Twin Peaks)']
['بهترین فیلم\u200cهای کمدی سال 2020 به ترتیب رتبه بندی که باید تماشا کنید']
what we recommend:
['پروشات - صفحه 6 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 5 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 4 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 8 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 2 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 3 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 9 از 348 - مجله آنلاین سینما و سرگرمی']
['پروشات - صفحه 10 از 348 - مجله آنلاین سینما و سرگرمی']
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
['7 فیلم جذاب و دیدنی شبیه فیلم “نقشه چیزهای کوچک عالی” (The Map of Tiny Perfect Things)']
['معرفی کارگردان\u200cهایی با بیشترین تعداد جایزه اسکار که باید آثارشان را تماشا کنید']
['پروشات - صفحه 11 از 348 - مجله آنلاین سینما و سرگرمی']
['10 پیچش دا

---user: b1a4daac-f564-4529-c5d1-efb031f894de ---
what user saw:
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
['لیست 20 تایی از بهترین فیلم های ژانر کودک در سال 2019-2020 - پروشات']
['20 فیلم برتر کودک و نوجوان - پروشات']
what we recommend:
['10 فیلم جذاب و دیدنی درباره نوجوانان در سال 2019 که باید تماشا کنید - پروشات']
['لیست بهترین انیمیشن هایی که در سال 2018 اکران شدند - پروشات']
['بهترین انیمیشن های سال 2019-2020 که حتما باید تماشا کنید - پروشات']
['7 فیلم جذاب و دیدنی شبیه فیلم "آرتمیس فاول" (Artemis Fowl) که باید تماشا کنید - پروشات']
['معرفی 18 فیلم غم انگیز تاریخ سینما - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه مجموعه "هری پاتر" (Harry Potter) - پروشات']
['معرفی بهترین فیلم های ژانر فانتزی تاریخ سینما که باید تماشا کنید - پروشات']
['8 وِرد جادویی هری پاتر که دوست داشتیم واقعی باشند - پروشات']
['لیست بهترین فیلم های دنیل ردکلیف (Daniel Radcliffe) که باید تماشا کنید - پروشات']
['10 پرنسس محبوب دخترها در دنیای انیمیشن های دیزنی - پروشات']
['م

In [131]:
for i in range(0,len(users_recoms2), 14):
    print(i)
    check(users_recoms2, i)

0
---user: 02fb517a-85ee-4e5e-ce00-50c8f3c384d2 ---
what user saw:
['معرفی 25 فیلم با پیچیده ترین پایان بندی ها در تاریخ سینما - پروشات']
['12 فیلم برتر تاریخ سینما با محوریت CIA (سازمان سیا) - پروشات']
['لیست بهترین فیلم هایی که با موضوع فرار از زندان ساخته شده اند - پروشات']
['معرفی 10 فیلم جذاب و دیدنی درباره تروریسم که شاید دوست داشته باشید تماشا کنید - پروشات']
what we recommend:
['20 فیلم برتر ژانر آدم ربایی در تاریخ سینما که باید ببینید - پروشات']
['25 فیلم روان شناسی تاریخ سینما که اثری عمیق روی شما می گذارند - پروشات']
['10 فیلم انتقامی برتر تاریخ سینما که باید ببینید - پروشات']
['معرفی بهترین فیلم های تاریخ سینما با موضوع اعتیاد و مواد مخدر - پروشات']
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['معرفی 26 فیلم جذاب و دیدنی درباره سرقت در تاریخ سینما که باید تماشا کنید - پروشات']
['معرفی 20 فیلم برتر سینما که ذهن بیننده را به چالش می کشند - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروش

['10 انیمه جذاب و دیدنی که از “دراگون بال” (Dragon Ball) الهام گرفته\u200cاند']
['10 انیمه شبیه ناروتو (Naruto) که باید تماشا کنید - پروشات']
['بهترین انیمه\u200cهای موردانتظار و نادیده گرفته شده سال 2021']
['7 انیمه جذاب و دیدنی شبیه “هوریمیا” (Horimiya) که باید تماشا کنید']
['15 انیمه جذاب و دیدنی شبیه “دکتر استون” (Dr. Stone) که باید تماشا کنید']
['لیست 30 شخصیت برتر در تاریخ انیمه ها - پروشات']
['لیست بهترین انیمه های جهان، 21 انیمه سینمایی برای چند بار دیدن! - پروشات']
154
---user: cd0c4d50-0847c-c54de-e21f8-8c233981e582e ---
what user saw:
['اگر به بازی GTA علاقه دارید، این 10 بازی را از دست ندهید - پروشات']
['لیست 20 تایی خشن ترین فیلم های تاریخ سینما که نباید از دست بدهید - پروشات']
['معرفی تمام فیلم های تام کروز از بدترین تا بهترین، 42 اثر سینمایی پرخرج - پروشات']
['9 فیلم جذاب و دیدنی شبیه فیلم "لوسی" (Lucy) که باید تماشا کنید - پروشات']
['معرفی 30 فیلم جذاب و دیدنی شبیه "تلقین" (Inception) - پروشات']
['50 بازی برتر در تاریخ بازی های کامپیوتری: از نوستالژیک ها تا مدرن ها - پر

['لیست بهترین سریال\u200cهای کره\u200cای سال 2020 که در انتظار پخششان هستیم - پروشات']
['بهترین سریال های درام کره ای که در سال 2019 پخش خواهند شد - پروشات']
['معرفی 18 سریال جذاب و دیدنی شبیه "دختر جدید" (New Girl) - پروشات']
['بهترین فیلم\u200cهای عجیب کمدی که شاید تا به حال تماشا نکرده باشید']
['7 فیلم جذاب و دیدنی شبیه فیلم "بعد از برخورد ما" (After We Collided) که باید تماشا کنید - پروشات']
336
---user: 0f6d13c1-5897-49f2-c961-25385d75cc29 ---
what user saw:
['بهترین انیمه های اکشن که تاکنون ساخته شده اند - پروشات']
['معرفی 20 انیمه مورد انتظار سال 2020 که در انتظار انتشارشان هستیم - پروشات']
['10 انیمه جذاب شبیه توکیو غول که باید تماشا کنید - پروشات']
['معرفی 11 انیمه جذاب و دیدنی با موضوع جادو و جادوگری - پروشات']
['معرفی 9 انیمه جذاب و دیدنی شبیه "دبیرستان مردگان" (Highschool of the Dead) - پروشات']
['بهترین انیمه های سینما با موضوع سفر در زمان - پروشات']
['11 انیمه برتر تاریخ با موضوع فرشتگان که باید ببینید - پروشات']
['لیست بهترین انیمه های 2018 که حتما باید ببینید - پروشات']

['لیست 25 تایی قوی\u200cترین اعضای تیم انتقام\u200cجویان در تاریخ کمیک\u200cهای مارول - پروشات']
['رتبه\u200cبندی باهوش\u200cترین ویلن\u200cهای فاز سوم دنیای سینمایی مارول']
['مبارزه ثور و سوپرمن؛ کدامیک در نبرد مرگ پیروز می\u200cشوند؟ - پروشات']
['رده بندی تمام اعضای انتقامجویان، از قویترین تا ضعیف ترین - پروشات']
['۵ قهرمان DC که می\u200cتوانند مرد عنکبوتی را شکست دهند (و ۵ تن که از او شکست می\u200cخورند) - پروشات']
['معرفی تاریخچه حق امتیاز شخصیت\u200cهای مارول - پروشات']
['جزئیات پنهان درباره لباس شخصیت\u200cهای "انتقام\u200cجویان" (The Avengers) - پروشات']
['25 شخصیت قدرتمند دنیای مارول از بین ابرقهرمانان و ابرشرورها - پروشات']
546
---user: 2e5e9938-0035-4066-c0a6-bc01c6b4b2fa ---
what user saw:
['معرفی 15 سریال جذاب و دیدنی شبیه "فرار از زندان" (Prison Break) - پروشات']
['معرفی 15 سریال جذاب و دیدنی شبیه "برکینگ بد" (Breaking Bad) - پروشات']
['معرفی 11 سریال جذاب و دیدنی شبیه "پانیشر" (The Punisher) - پروشات']
what we recommend:
['معرفی 14 سریال جذاب و دیدنی شبیه "100" - پروشات']

['بهترین فیلم\u200cهای ژانر بقا و نجات از مرگ (Survival) در تاریخ سینما - پروشات']
['معرفی بهترین فیلم های ژانر فانتزی تاریخ سینما که باید تماشا کنید - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه مجموعه "اره" (Saw) - پروشات']
['10 فیلم جذاب و دیدنی شبیه فیلم "احضار" (The Conjuring) - پروشات']
['بهترین فیلم های علمی تخیلی در قرن 21 (تا به اینجا) - پروشات']
['معرفی 12 سریال جذاب و دیدنی شبیه "مردگان متحرک" (The Walking Dead) - پروشات']
['بهترین فیلم های زامبی سال 2019-2020 کدام اند؟ - پروشات']
770
---user: ce6cbbca-ac284-4db00-00f14-40f940edd5a16 ---
what user saw:
['لیست بهترین فیلم های فضایی کل تاریخ سینما - از ادیسه فضایی تا میان ستاره ای - پروشات']
['20 فیلم کارآگاهی و رمزآلود برتر در تاریخ سینما - پروشات']
['15 فیلم ترسناک برتر درباره بیگانگان که باید تماشا کنید - پروشات']
['نگاهی به بهترین فیلم های مارک والبرگ (بازیگر) - پروشات']
['12 فیلم با جلوه های بصری مبهوت کننده که حتی میتوانید بدون صدا تماشا کنید - پروشات']
['10 فیلم جذاب و دیدنی شبیه فیلم "محرمانه لس آنجلس" (L.A. Confidentia

...

---user: f049a300-8a32-4e0d-ceb2-ed7978ab11e6 ---
what user saw:
['12 فیلم و سریال برتر تاریخ درباره وایکینگ ها - پروشات']
['12 فیلم جذاب و دیدنی شبیه فیلم "مومیایی" (The Mummy) که باید تماشا کنید - پروشات']
['لیست بهترین فیلم\u200cهای عجیب و غریب تاریخ سینما که باید تماشا کنید']
what we recommend:
['معرفی 10 فیلم جذاب و دیدنی شبیه "گلادیاتور" (Gladiator) - پروشات']
['بهترین فیلم هایی خارجی که در فضای قرون وسطی ساخته شده اند - پروشات']
['15 فیلم برتر تاریخ سینما با موضوع اژدها که باید تماشا کنید - پروشات']
['8 فیلم برتر تاریخ درباره خدایان و اساطیر یونان به همراه تریلر - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه سه گانه "ارباب حلقه ها" (The Lord of the Rings) - پروشات']
['10 فیلم جذاب و دیدنی شبیه فیلم "خون زئوس" (Blood Of Zeus) که باید تماشا کنید - پروشات']
['7 سریال جذاب و دیدنی شبیه سریال "مردان اسکاندیناوی" (Norsemen) که باید تماشا کنید - پروشات']
['لیست بهترین فیلم\u200cهای ناراحت کننده و عذاب آور تاریخ سینما']
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز

---user: dcd5c5e5-e222-4128-c1f6-95ab9974bfa7 ---
what user saw:
['معرفی فیلم های جذاب و دیدنی مشابه "زندگی ادل" (Blue is the Warmest Color) - پروشات']
['معرفی 18 فیلم غم انگیز تاریخ سینما - پروشات']
['بهترین فیلم های عاشقانه غم انگیز در تاریخ سینما - پروشات']
what we recommend:
['معرفی 18 فیلم جذاب و دیدنی این دهه درباره افراد دگرباش (LGBT) - پروشات']
['معرفی بهترین فیلم های عاشقانه قرن 21 که احساسات شما را برانگیخته می\u200cکنند - پروشات']
['لیست زننده\u200cترین و زجرآورترین فیلم\u200cهای تاریخ سینما که هرگز فراموش نخواهید کرد - پروشات']
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
['معرفی 15 فیلم جذاب و دیدنی شبیه "پنجاه طیف خاکستری" (Fifty Shades of Grey) - پروشات']
['7 فیلم جذاب و دیدنی شبیه فیلم "بعد از برخورد ما" (After We Collided) که باید تماشا کنید - پروشات']
['بهترین فیلم های عاشقانه سال 2019 که نباید از دست بدهید - پروشات']
['معرفی 10 فیلم جذاب و دیدنی شبیه "بخت پریشان" (The Fault In Our Stars) - پروشات']
['بهترین فیلم های تاریخ سینما در

['برترین فیلم\u200cهای قرن بیستم در مورد جادو و تردستی - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه سه گانه "ارباب حلقه ها" (The Lord of the Rings) - پروشات']
['لیست بهترین فیلم های فانتزی خارجی که در سال 2018 اکران شدند - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه مجموعه "هری پاتر" (Harry Potter) - پروشات']
['معرفی بهترین فیلم\u200cها درباره "پری دریایی" که باید تماشا کنید - پروشات']
['معرفی بهترین سیکوئل فیلم\u200cهای ابرقهرمانی که باید آنها را تماشا کنید']
['بهترین فیلم\u200cهای خون آشامی عاشقانه در تاریخ سینما - پروشات']
['بهترین فیلم های کمپانی دیزنی که در سال 2019-2020 اکران خواهند شد - پروشات']
['بهترین فیلم های سینمایی کره ای رمانتیک که باید ببینید - پروشات']
['7 فیلم جذاب و دیدنی شبیه فیلم "مالیفیسنت" (Maleficent) - پروشات']
['معرفی 17 فیلم جذاب و دیدنی درباره نوجوانان در این دهه (2019 تا 2010) - پروشات']
14210
---user: 6911b2d4-fff0-4ecb-ce52-ad2e44f39981 ---
what user saw:
['معرفی 10 فیلم جذاب و دیدنی شبیه "درخشش ابدی یک ذهن پاک" (Eternal Sunshine of the Spotless Mind) - پرو

---user: 3572bf17-7e56f-f0054-4394f-fb8c38e16f0af ---
what user saw:
['بهترین فیلم های علمی تخیلی در قرن 21 (تا به اینجا) - پروشات']
['بهترین فیلم\u200cهای خون آشامی عاشقانه در تاریخ سینما - پروشات']
['لیست بهترین فیلم های خون آشامی که در سال 2018 اکران شدند - پروشات']
['معرفی 15 فیلم جذاب و دیدنی شبیه "گرگ و میش" (Twilight) - پروشات']
['9 فیلم جذاب و دیدنی شبیه فیلم "لوسی" (Lucy) که باید تماشا کنید - پروشات']
['آیا می\u200cدانستید این سلبریتی\u200cها سیگار می\u200cکشند؟ - پروشات']
['17 حقیقت پشت صحنه فیلم "تایتانیک" (Titanic) که از آن خبر نداشتید - پروشات']
['معرفی 12 فیلم جذاب و دیدنی شبیه مجموعه “هری پاتر” (Harry Potter)']
['آخر هفته با طعم فیلم! (شماره 114)']
['لیست بهترین فیلم\u200cها درباره مشکلات خانوادگی که باید تماشا کنید']
what we recommend:
['12 فیلم جذاب و دیدنی شبیه فیلم "دونده مارپیچ" (The Maze Runner) - پروشات']
['معرفی بهترین فیلم\u200cهای مشابه “بااستعداد” (Gifted) که باید تماشا کنید']
['معرفی 9 فیلم درباره خون آشام\u200cها و گرگینه\u200cها که در آینده نزدیک اکران خواه

['معرفی 10 انیمه سریالی جذاب و دیدنی برای طرفداران انیمه - پروشات']
['بهترین انیمه\u200cهای موردانتظار و نادیده گرفته شده سال 2021']
14686
---user: 1ae0d841-f5b2-40d4-c023-caa2908cba4c ---
what user saw:
['25 ابر قهرمان قدرتمند تمام زمان\u200cها به همراه تصاویر - پروشات']
['رده بندی تمام اعضای انتقامجویان، از قویترین تا ضعیف ترین - پروشات']
['لیست قدرتمندترین سلاح\u200cها در دنیای کمیک\u200cهای مارول - پروشات']
['لیست 25 تایی قوی\u200cترین اعضای تیم انتقام\u200cجویان در تاریخ کمیک\u200cهای مارول - پروشات']
['جزئیات پنهان درباره لباس شخصیت\u200cهای "انتقام\u200cجویان" (The Avengers) - پروشات']
what we recommend:
['10 حقیقت درباره مرد آهنی که از آن خبر ندارید - پروشات']
['لیست قدرتمندترین ویلن\u200cهایی که در مقابل اسکارلت ویچ شکست خورده\u200cاند - پروشات']
['معرفی 18 نسخه کمیکی از شخصیت ثور، از جوان\u200cترین تا قدرتمندترین - پروشات']
['تمام بازیگرانی که در “مرد عنکبوتی 3” به شخصیت\u200cهای خود بازمی\u200cگردند']
['10 شخصیت مارول که از دی سی الهام گرفته شده اند - پروشات']
['معرفی تمام چ